## Plus Court Chemin dans un Graphe Pondéré

Dans cette partie, on essaye de trouver le chemin le plus court pour aller d'un point à un autre sur une carte.
Pour cela, on peut utiliser des parcours de graphes.

**Question 0.** Quel type de parcours de graphes utiliser pour trouver le plus court chemin entre deux points ?

*Réponse :*

#### Terrain de jeu.

In [ ]:
import numpy as np
import networkx as nx
import matplotlib.pyplot as plt

In [ ]:
from matplotlib.collections import LineCollection
from matplotlib.colors import ListedColormap
cmap = ListedColormap(["sandybrown", "aquamarine"])

def afficher_terrain(terrain, chemin=None):
    plt.imshow(terrain, cmap=cmap)
    plt.axis("off");
    
    if chemin is not None:
        solx = [v for (u, v) in chemin]
        soly = [u for (u, v) in chemin]
        plt.plot(solx, soly, color="red")

La fonction ci-dessus permet d'afficher un terrain de jeu, représenté sous la forme d'une matrice.
Prenons le terrain suivant, où la terre est représentée en marron et l'eau en bleu.

In [ ]:
terrain = np.zeros((10, 10))
terrain = np.array(
      [[0, 0, 1, 1, 0, 0, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0, 1, 0, 0, 0],
       [0, 1, 1, 0, 0, 1, 1, 1, 0, 0],
       [0, 1, 1, 0, 1, 1, 1, 1, 1, 0],
       [0, 0, 1, 0, 0, 1, 1, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 0, 1, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 1, 1, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 1, 1, 0, 0, 0]])

afficher_terrain(terrain)

#### Coûts des Déplacements.

Représentons ce terrain sous la forme d'un graphe pondéré.
Les sommets du graphe seront les cases du terrain, la case de coordonnées $(x, y)$ ayant pour nom $(x, y)$.

Supposons que l'on puisse facilement se déplacer d'une case de terre à un autre, et que l'on se déplace avec un peu plus de difficulté dans l'eau.
En revanche, on n'a vraiment pas envie de se mouiller, donc passer d'une case de terre à une case d'eau nous demande beaucoup de préparations et d'énergie.

Résumons cela par les règles de déplacements suivantes :
* passer d'une case de terre à une case de terre a un coût de $1$ ;
* passer d'une case d'eau à une case d'eau a un coût de $2$ ;
* passer d'une case de terre à une d'eau ou le contraire a un coût de $200$.

On peut alors traduire notre carte par un graphe pondéré, dont les poids sont ceux décrits au dessus.

Les fonctions suivantes sont des fonctions qui génèrent le graphe correspondant au terrain et des fonctions d'affichage.

In [ ]:
def valeur(u, v, val_eau=200):
    if u + v == 0:
        return 1
    if u + v == 1:
        return val_eau
    else:
        return 2
    
valeur_normale = lambda u, v: valeur(u, v, 200)
valeur_nulle = lambda u, v: valeur(u, v, 0)

def graphe_terrain(terrain, valeur=valeur_normale):
    width, height = terrain.shape
    
    aretes_poids =  [((u, v), (u+1,v), valeur(terrain[u,v], terrain[u+1,v])) \
                      for u in range(width - 1) for v in range(height)]
    aretes_poids += [((u, v), (u,v+1), valeur(terrain[u,v], terrain[u,v+1])) \
                      for u in range(width) for v in range(height-1)]
    
    G = nx.Graph()
    G.add_weighted_edges_from(aretes_poids)
    
    return G


def afficher_graphe_terrain(Gterrain, terrain):
    fig, ax = plt.subplots(figsize=(10,10))

    pos = {(u, v): (v, terrain.shape[0]-u) for u in range(terrain.shape[0]) for v in range(terrain.shape[1])}
    aretes_poids = {(u,v,): d['weight'] for u,v,d in Gterrain.edges(data=True)}

    nx.draw(Gterrain, pos,
        node_color=["sandybrown" if terrain[u] == 0 else "aquamarine" for u in Gterrain.nodes()],
        edgecolors="black")
    nx.draw_networkx_edge_labels(Gterrain,pos,edge_labels=aretes_poids);


#### Graphe des déplacements.

Affichons le graphe correspondant au terrain ci-dessus.
Les sommets du graphe ont pour étiquette les coordonées $(x, y)$ de la case du terrain à laquelle ils correspondent, et les arêtes sont pondérées par le coût du passage d'un sommet à un autre.

In [ ]:
Gterrain = graphe_terrain(terrain)

afficher_graphe_terrain(Gterrain, terrain)

Voilà une fonction qui prend un graphe en entrée et qui renvoit sa liste d'adjacence.

In [ ]:
def liste_adjacence(G):
    adj = {}
    
    for sommet, adjacence in G.adjacency():
        adj[sommet] = adjacence.keys()
        
    return adj

#### Recherche de Chemin.

Pour trouver le chemin le plus court dans ce graphe pondéré, on procède comme pour trouver le chemin le plus court dans un graphe non pondéré.

On part donc d'un sommet, puis on visite ses voisins, et ainsi de suite.
Seulement, quand on rencontre un nouveau voisin, on a deux possibilités :
* soit on ne l'a jamais rencontré, et le chemin actuel est le plus court pour l'instant ;
* soit on l'a déjà rencontré, auquel cas, soit le chemin actuel est plus court, et peut donc remplacer le chemin déjà connu, soit il est plus long, et on peut l'ignorer.

On ne gardera donc plus en mémoire l'ensemble des sommets que l'on a déjà visités, mais la longueur du chemin le plus court que l'on connaît jusqu'à ce sommet.

**Question 1.** Implémentez une fonction `plus_court_chemin` qui prend en entrée un graphe pondéré et qui renvoit le plus court chemin (sous la forme d'une liste de sommets) entre les deux sommets s'il en existe un, et qui renvoie `False` sinon.

On pourra garder en mémoire :
* une queue`a_visiter` (utiliser par exemple `deque`) des sommets qui restent à visiter ;
* un dictionnaire `predecesseur` qui associe à chaque sommet son prédécesseur dans le chemin le plus court connu jusqu'ici ;
* un dictionnaire `distance` qui associe à chaque sommet sa distance au sommet de départ. Au début, ce dictionnaire associera la valeur `np.inf` à tous les sommets sauf au sommet de départ, auquel il associera `0`. De cette façon, on pourra facilement calculer si le chemin courant est plus court ou plus long qu'un chemin déjà connu.

Remarques :
* on peut récupérer le poids d'une arête $(u, v)$ en utilisant : `poids = G.get_edge_data(u, v)["weight"]` ;
* la fonction `liste_adjacence` ci-dessus renvoie la liste d'adjacence du graphe sous forme d'un dictionnaire dont les valeurs sont les listes d'adjacences et les clés les sommets (comme en TP).

In [ ]:
from collections import deque

def plus_court_chemin(G, s1, s2):
    # ~~~ implémeter la fonction ~~~

**Question 2.** Utilisez votre fonction pour afficher le plus court chemin partant d'en haut à gauche (sommet $(0, 0)$) jusqu'au sommet en bas à droite (sommet $(9, 9)$).

Vous pourrez utiliser la fonction `afficher_terrain` en lui donnant `terrain` comme premier argument et votre chemin se second argument.

In [ ]:
afficher_terrain(terrain, chemin)

Supposons maintenant que l'on ait extrêmement envie de plonger, et donc que, maintenant, passer de la terre ferme à l'eau a un coût de $0$.

Le graphe correspondant aux coûts de déplacements sur notre terrain est donc maintenant le suivant :

In [ ]:
Gterrain0 = graphe_terrain(terrain, valeur_nulle)
afficher_graphe_terrain(Gterrain0, terrain)

**Question 3.** Avec ces nouvelles règles de déplacement, affichez le plus court chemin entre les sommets $(0, 0)$ et $(9, 9)$.

In [ ]:
afficher_terrain(terrain, chemin0)

**Question 4.** Commentez le chemin obtenu. Est-ce bien le chemin le plus court ?

*Réponse :*